In [23]:
import os
import sys
import six
import glob
import math
import pandas as pd
import numpy as np
from keras.utils import to_categorical
import scipy.ndimage as nd
from scipy.ndimage import zoom
import random

In [169]:
import keras
import tensorflow as tf
from keras import Model
from keras import backend as K
from keras.regularizers import l2
from keras.engine import Layer,InputSpec
from keras.layers.merge import concatenate
from keras.callbacks import TensorBoard,Callback
from keras.layers.advanced_activations import LeakyReLU
from keras.preprocessing.image import ImageDataGenerator
from keras.layers.normalization import BatchNormalization
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras import initializers, regularizers, constraints,optimizers
from keras.callbacks import ModelCheckpoint, LearningRateScheduler,TensorBoard
from keras.layers import Add,Input,Conv3D,Convolution3D,Dropout,UpSampling3D,Concatenate,MaxPooling3D,Dot,\
GlobalAveragePooling3D,Dense,GlobalMaxPooling3D,Lambda,Activation,Reshape,Permute, PReLU, Deconvolution3D,\
Multiply,GlobalAveragePooling3D,Dense,Softmax

In [25]:
sys.path.append('../baseLayers/')

In [26]:
from InstanceNorm import InstanceNormalization

In [27]:
num_blocks = 5
# strides = [2,2,2,2,2]
strides = [1,2,2,2,2]
nodule_seg_strides = [1,2,2,2,2]
# atrous_rates = [1,1,2,4,8]
atrous_rates = [1,1,1,1,1]
base_filters = 32
norm_func = InstanceNormalization
activation_func = LeakyReLU
kernel_size = 3
padding = 'same'
dropout_rate = 0
input_shape = (32,64,64,1)
num_classes = 1

In [28]:
from ResNet import Resnet3DBuilder
from VGGmodel import VGG
from NoduleSegEncoder import NoduleSegEncoder_proxima


In [29]:
from CommonLayers import *
# from NoduleSegDecoder import NoduleSegDecoder_proxima
sys.path.append('../decoders/')
from NoduleSegDecoder import NoduleSegDecoder_proxima

In [30]:
parameter_list = {
    'num_blocks':num_blocks,
    'strides':strides,
    'atrous_rates':atrous_rates,
    'base_filters':base_filters,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'dropout_rate':dropout_rate,
    'num_classes':1,
    'classification_layers':GlobalMaxPooling3D
}

In [31]:
resnet_parameter_list = {
    'base_filters':base_filters,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'dropout_rate':dropout_rate,
    'num_classes':1,
    'classification_layers':GlobalMaxPooling3D,
    'init_kernel_size':1
}

In [32]:
noduleseg_parameter_list = {
    'num_blocks':num_blocks,
    'strides':nodule_seg_strides,
    'atrous_rates':[1 for _ in range(num_blocks)],
    'base_filters':base_filters,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'dropout_rate':0.5,
    'num_classes':1,
    'classification_layers':GlobalMaxPooling3D
}

In [33]:
result = NoduleSegEncoder_proxima(input_shape,**noduleseg_parameter_list)

In [34]:
result[1]

[<tf.Tensor 'input_4:0' shape=(?, 32, 64, 64, 1) dtype=float32>,
 <tf.Tensor 'NoduleSegEncoderDropout01_1/cond/Merge:0' shape=(?, 16, 32, 32, 32) dtype=float32>,
 <tf.Tensor 'NoduleSegEncoderDropout02_1/cond/Merge:0' shape=(?, 8, 16, 16, 64) dtype=float32>,
 <tf.Tensor 'NoduleSegEncoderDropout03_1/cond/Merge:0' shape=(?, 4, 8, 8, 128) dtype=float32>,
 <tf.Tensor 'NoduleSegEncoderDropout04_1/cond/Merge:0' shape=(?, 2, 4, 4, 256) dtype=float32>,
 <tf.Tensor 'NoduleSegEncoderDropout05_1/cond/Merge:0' shape=(?, 1, 2, 2, 512) dtype=float32>]

In [35]:
result1 = VGG(input_shape,**parameter_list)

In [36]:
resnet_builder = Resnet3DBuilder(**resnet_parameter_list)
result_res = resnet_builder.build_resnet_50(input_shape)

In [37]:
noduleseg_decoder_parameter_list = {
   'kernel_initializer':'he_normal',
    'kernel_regularizer':l2(1e-4),
    'kernel_size':kernel_size,
    'final_kernel_size':1,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'seg_num_class':2,
    'merge_axis':-1,
    'SEB_choice':True,
    'ACR_choice':False,
    'OCR_choice':False,
    'deep_supervision':True,
    'num_units':[3,3,3,3]
    
    
    
    
}

In [38]:
model = NoduleSegDecoder_proxima(result,**noduleseg_decoder_parameter_list)

('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(2), Dimension(4), Dimension(4), Dimension(256)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(4), Dimension(8), Dimension(8), Dimension(128)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(8), Dimension(16), Dimension(16), Dimension(64)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(16), Dimension(32), Dimension(32), Dimension(32)]))


../decoders/NoduleSegDecoder.py:247: UserWarning: Update your `Conv3D` call to the Keras 2 API: `Conv3D(kernel_initializer="he_normal", name="NoduleSegDecoder_conv3d_mins1", activation="softmax", padding="same", kernel_regularizer=<keras.reg..., filters=2, kernel_size=1)`
  border_mode='same',activation=current_acti,name='NoduleSegDecoder_conv3d_mins1')
../decoders/NoduleSegDecoder.py:54: UserWarning: Update your `Conv3D` call to the Keras 2 API: `Conv3D(kernel_initializer="he_normal", name="NoduleSegDecoder_DeepSupervision_block01_conv", activation="softmax", padding="same", kernel_regularizer=<keras.reg..., filters=2, kernel_size=1)`
  border_mode=padding,activation=current_acti,name='%s_conv'%block_pre)(x)
../decoders/NoduleSegDecoder.py:54: UserWarning: Update your `Conv3D` call to the Keras 2 API: `Conv3D(kernel_initializer="he_normal", name="NoduleSegDecoder_DeepSupervision_block02_conv", activation="softmax", padding="same", kernel_regularizer=<keras.reg..., filters=2, kernel_si

In [39]:
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 32, 64, 64, 1 0                                            
__________________________________________________________________________________________________
NoduleSegConvBlock01_conv_01 (C (None, 16, 32, 32, 3 896         input_4[0][0]                    
__________________________________________________________________________________________________
NoduleSegConvBlock01_norm_01 (I (None, 16, 32, 32, 3 2           NoduleSegConvBlock01_conv_01[0][0
__________________________________________________________________________________________________
NoduleSegConvBlock01_activation (None, 16, 32, 32, 3 0           NoduleSegConvBlock01_norm_01[0][0
__________________________________________________________________________________________________
NoduleSegC

In [40]:
model1 = NoduleSegDecoder_proxima(result1,**noduleseg_decoder_parameter_list)

('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(4), Dimension(8), Dimension(8), Dimension(256)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(8), Dimension(16), Dimension(16), Dimension(128)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(16), Dimension(32), Dimension(32), Dimension(64)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(32), Dimension(64), Dimension(64), Dimension(32)]))


In [41]:
model1.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_5 (InputLayer)            (None, 32, 64, 64, 1 0                                            
__________________________________________________________________________________________________
VGG_block01_conv_01 (Conv3D)    (None, 32, 64, 64, 3 896         input_5[0][0]                    
__________________________________________________________________________________________________
VGG_block01_norm_01 (InstanceNo (None, 32, 64, 64, 3 2           VGG_block01_conv_01[0][0]        
__________________________________________________________________________________________________
VGG_block01_activation_01 (Leak (None, 32, 64, 64, 3 0           VGG_block01_norm_01[0][0]        
__________________________________________________________________________________________________
VGG_block0

In [42]:
model2 = NoduleSegDecoder_proxima(result_res,**noduleseg_decoder_parameter_list)

('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(4), Dimension(8), Dimension(8), Dimension(256)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(8), Dimension(16), Dimension(16), Dimension(128)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(16), Dimension(32), Dimension(32), Dimension(64)]))
('decoder_tensor shape is ', TensorShape([Dimension(None), Dimension(32), Dimension(64), Dimension(64), Dimension(32)]))


In [ ]:
model2.summary()

In [118]:
def SpatialGather(x,probs):
    '''
    x represents features and probs represents coarse segmentation prob map
    '''
    
    batch_size,depth,height,width,num_classes = probs._keras_shape
    upsample_ratio = int(depth/x._keras_shape[1])
    if upsample_ratio>1:
        x = UpSampling3D(size=upsample_ratio,name='SpatialGather')(x)

    num_features = x._keras_shape[-1]
    
    reshape_x = Reshape(target_shape=(depth*height*width,num_features))(x)
    reshape_probs = Reshape(target_shape=(depth*height*width,num_classes))(probs)
    
    result = Dot(axes=1)([reshape_probs,reshape_x])
    result = Reshape(target_shape=(1,1,result._keras_shape[1],result._keras_shape[2]))(result)
    return result
    

In [220]:
def OCRModule(x,proxy,**kwargs):
    
    norm_func = kwargs.get('norm_func')
    activation_func = kwargs.get('activation_func')
    num_filters = kwargs.get('num_filters')
    kernel_size = kwargs.get('kernel_size',1)
    padding = kwargs.get('padding','same')

    atrous_rate = kwargs.get('atrous_rate',1)
    conv_first = kwargs.get('conv_first',True)
    dropout_rate= kwargs.get('dropout_rate',0)
    kernel_initializer = kwargs.get('kernel_initializer','he_normal')
    kernel_regularizer = kwargs.get('kernel_regularizer',l2(1e-4))
    
    block_prefix = 'OCRModule'
    
    input_features = x._keras_shape[-1]
    query = x
    for layer_idx in range(2):
        query = ConvUnit(query,norm_func=norm_func,activation_func=activation_func,num_filters=num_filters,
                    kernel_size=kernel_size,atrous_rate=atrous_rate,padding=padding,block_prefix=block_prefix+'_query',
                     kernel_initializer=kernel_initializer,kernel_regularizer=kernel_regularizer,
                    layer_idx=layer_idx+1,conv_first=conv_first)
    
    key,value = proxy,proxy
    for layer_idx in range(2):
        key = ConvUnit(key,norm_func=norm_func,activation_func=activation_func,num_filters=num_filters,
                    kernel_size=kernel_size,atrous_rate=atrous_rate,padding=padding,block_prefix=block_prefix+'_key',
                     kernel_initializer=kernel_initializer,kernel_regularizer=kernel_regularizer,
                    layer_idx=layer_idx+1,conv_first=conv_first)
    value = ConvUnit(value,norm_func=norm_func,activation_func=activation_func,num_filters=num_filters,
                    kernel_size=kernel_size,atrous_rate=atrous_rate,padding=padding,block_prefix=block_prefix+'_value',
                     kernel_initializer=kernel_initializer,kernel_regularizer=kernel_regularizer,
                    layer_idx=1,conv_first=conv_first)
    
    batch,query_depth,query_height,query_width,query_filters = query._keras_shape
    batch,key_depth,key_height,key_width,key_filters = key._keras_shape
    
    query = Reshape(target_shape=(query_depth*query_height*query_width,query_filters))(query)
    
    key = Reshape(target_shape=(key_depth*key_height*key_width,key_filters))(key)
    value = Reshape(target_shape=(key_depth*key_height*key_width,key_filters))(value)
    value = Permute(dims=[2,1])(value)

    sim_map = Dot(name='%s_SimMapDot'%block_prefix,axes=2)([query,key])
    sim_map = Softmax(axis=-1,name='%s_SimMapSoftmax'%block_prefix)(sim_map)
    
    context = Dot(axes=2)([sim_map,value])

    context = Reshape(target_shape=(query_depth,query_height,query_width,query_filters))(context)
    
    combine_feature = Concatenate()([x,context])
    
    final_result = ConvUnit(combine_feature,norm_func=norm_func,activation_func=activation_func,num_filters=input_features,
                    kernel_size=kernel_size,atrous_rate=atrous_rate,padding=padding,block_prefix=block_prefix+'_FinalCombine',
                     kernel_initializer=kernel_initializer,kernel_regularizer=kernel_regularizer,
                    layer_idx=1,conv_first=conv_first)
    return final_result

In [221]:
# for layer_idx,layer in enumerate(model.layers):
#     print ('='*60)
#     print ('layer_idx',layer_idx)
#     print layer.output.shape

In [222]:
x = model.layers[124].output
probs = model.layers[131].output

In [223]:
proxy = SpatialGather(x,probs)

In [224]:
temp_parameter_list = {
    'norm_func':norm_func,
    'num_filters':128,
    'kernel_size':1,
    'padding':'same',
    'atrous_rates':1,
    'kernel_initializer':'he_normal',
    'kernel_regularizer':None
    
}

In [225]:
OCRModule(x,proxy,**temp_parameter_list)

<tf.Tensor 'OCRModule_FinalCombine_norm_01/add_1:0' shape=(?, 8, 16, 16, 8) dtype=float32>

In [219]:
proxy.shape

TensorShape([Dimension(None), Dimension(1), Dimension(1), Dimension(2), Dimension(8)])